In [2]:
import pandas as pd
from googleapiclient.errors import HttpError

df = pd.read_excel('demo.xlsx')

In [21]:
df

KeyError: 'impression'

In [23]:
# Grab the Column E
impression_column = df.iloc[:, 4]
total_impressions = impression_column[impression_column.shift(-1).isna()].iloc[0]

total_impressions


71796.3

Addresses Sum of New Road Duration (Mins)  \
27                     Total                         16041.4   
30  Target (Total Campaigns)                          144000   
34  Target (Total Campaigns)                            2400   
45                     Total                         16041.4   
52                     Total                         16041.4   
59                     Total                         16041.4   
65                     Total                         16041.4   
73                     Total                         16041.4   
80                     Total                           15180   
88                     Total                         16041.4   
93                     Total                         16041.4   

   Sum of New Road Duration (Hours)       % Impression     %.1 Unnamed: 6  \
27                            267.4  100.0%    71796.3  100.0%        NaN   
30                             100%     NaN        NaN     NaN        NaN   
34                              100     NaN        NaN     NaN        NaN   
45                            267.4  100.0%    71796.3  100.0%        NaN   
52                            267.4  100.0%    71796.3  100.0%        NaN   
59                          21915.9  115628       400%     NaN      Total   
65                            267.4  100.0%    71796.3  100.0%        NaN   
73                            267.4  100.0%    71796.3  100.0%        NaN   
80                              253  100.0%    67497.1  100.0%        NaN   
88                            267.4  100.0%    71796.3  100.0%        NaN   
93                            267.4  100.0%    71796.3  100.0%        NaN   

   Addresses.1 Sum of Idle Final (Mins) Sum of Idle Final (Hours)     %.2  
27       Total                  21915.9                     365.3  100.0%  
30   Idle Time             21915.866667                       NaN     NaN  
34         NaN                      NaN                       NaN     NaN  
45       Total                  21915.9                     365.3  100.0%  
52       Total                  21915.9                     365.3  100.0%  
59     16041.4                  21915.9                    115628    400%  
65       Total                  21915.9                     365.3  100.0%  
73       Total                  21915.9                     365.3  100.0%  
80       Total                  21228.8                     353.8  100.0%  
88       Total                  21915.9                     365.3  100.0%  
93       Total                  21915.9                     365.3  100.0%

In [30]:
from services import slides_service

# presentation_id = "1fgDkE5ODOQNQRMy71kiwvUJ4ZJ63DKncc2uDogyZgkM"
# presentation_id = "1WK34qF2PsBqdHMt_OEi_C0veuXFXYUzSKP-_g0A6Mlw"
presentation_id = "1rdL8zE2ayHtfPYeHf8KaBHWOD1hwgewfJrhhJYT9xik"

In [31]:
try:
    # Fetch the presentation details
    presentation = slides_service.presentations().get(
        presentationId=presentation_id
    ).execute()

    # Prepare the batch update requests
    requests = []

    # Loop through slides and elements
    for slide in presentation.get("slides", []):
        slide_id = slide.get("objectId")
        print(f"Processing Slide ID: {slide_id}")

        for element in slide.get("pageElements", []):
            element_id = element.get("objectId")

            # Check if the element is a shape with text
            if "shape" in element and "text" in element["shape"]:
                # Extract and log the text content
                text_elements = element["shape"]["text"].get("textElements", [])
                for text_element in text_elements:
                    if "textRun" in text_element:
                        text_content = text_element["textRun"].get("content", "").strip()
                        print(f"Text Content in Element ID {element_id}: '{text_content}'")

                # Append request to replace text with objectId
                requests.append(
                    {
                        "replaceAllText": {
                            "containsText": {
                                "text": "{{ANY_TEXT}}",  # Match all text
                                "matchCase": False
                            },
                            "replaceText": element_id
                        }
                    }
                )

    # Execute the batch update to replace all text
    if requests:
        response = slides_service.presentations().batchUpdate(
            presentationId = presentation_id,
            body={"requests": requests}
        ).execute()
        print("All text boxes have been updated with their object IDs.")
        # return response
    else:
        print("No text boxes found to update.")

except HttpError as error:
    print(f"An error occurred: {error}")
    # return None


Processing Slide ID: g1b8874900bb_0_309
Text Content in Element ID g1b8874900bb_0_312: 'campaign report'
Text Content in Element ID g1b8874900bb_0_316: 'Aegis'
Text Content in Element ID g1b8874900bb_0_316: ''
Text Content in Element ID g1b8874900bb_0_317: 'brand • entice • inspire'
Text Content in Element ID g1b8874900bb_0_318: 'prepared for:'
Processing Slide ID: g1b8874900bb_0_322
Text Content in Element ID g1b8874900bb_0_326: 'carching.co'
Text Content in Element ID g1b8874900bb_0_327: 'brand • entice • inspire'
Text Content in Element ID g1b8874900bb_0_328: '428.5k'
Text Content in Element ID g1b8874900bb_0_328: ''
Text Content in Element ID g1b8874900bb_0_330: 'Impressions'
Text Content in Element ID g1b8874900bb_0_331: '12.9k'
Text Content in Element ID g1b8874900bb_0_331: 'km'
Text Content in Element ID g1b8874900bb_0_331: ''
Text Content in Element ID g1b8874900bb_0_333: 'Distance Travelled'
Text Content in Element ID g1b8874900bb_0_334: '745.0'
Text Content in Element ID g1b8

In [32]:
# g1b8874900bb_0_328

# g1b8874900bb_0_431

In [33]:
from services import slides_service, sheets_service, drive_service

In [35]:
# Step 1: Create a Spreadsheet with Data
spreadsheet_body = {
    "properties": {"title": "Actual vs Target Data"}
}
spreadsheet = sheets_service.spreadsheets().create(body=spreadsheet_body).execute()
spreadsheet_id = spreadsheet['spreadsheetId']
print(f"Spreadsheet ID: {spreadsheet_id}")

# Populate with Data
data = [
    ["Metric", "Value"],
    ["Expected", 100.0],
    ["Actual", 101.1],
]
data_range = "Sheet1!A1:B3"
value_range_body = {"values": data}
sheets_service.spreadsheets().values().update(
    spreadsheetId=spreadsheet_id,
    range=data_range,
    valueInputOption="RAW",
    body=value_range_body
).execute()

# Step 2: Add a Horizontal Bar Chart
chart_body = {
    "requests": [
        {
            "addChart": {
                "chart": {
                    "spec": {
                        "title": "Actual vs Target",
                        "basicChart": {
                            "chartType": "BAR",
                            "legendPosition": "BOTTOM_LEGEND",
                            "axis": [
                                {"position": "BOTTOM_AXIS", "title": "Percentage"},
                                {"position": "LEFT_AXIS", "title": "Metric"},
                            ],
                            "domains": [
                                {
                                    "domain": {
                                        "sourceRange": {
                                            "sources": [
                                                {
                                                    "sheetId": 0,
                                                    "startRowIndex": 1,
                                                    "endRowIndex": 3,
                                                    "startColumnIndex": 0,
                                                    "endColumnIndex": 1,
                                                }
                                            ]
                                        }
                                    }
                                }
                            ],
                            "series": [
                                {
                                    "series": {
                                        "sourceRange": {
                                            "sources": [
                                                {
                                                    "sheetId": 0,
                                                    "startRowIndex": 1,
                                                    "endRowIndex": 3,
                                                    "startColumnIndex": 1,
                                                    "endColumnIndex": 2,
                                                }
                                            ]
                                        }
                                    },
                                    "targetAxis": "BOTTOM_AXIS",
                                }
                            ],
                            "stackedType": "STACKED",
                        },
                    },
                    "position": {"overlayPosition": {}},
                }
            }
        }
    ]
}

sheets_service.spreadsheets().batchUpdate(spreadsheetId=spreadsheet_id, body=chart_body).execute()
print("Chart created in Google Sheets")

# Step 3: Create a Google Slide Presentation
presentation = slides_service.presentations().create(body={"title": "Actual vs Target Chart"}).execute()
presentation_id = presentation['presentationId']
print(f"Presentation ID: {presentation_id}")

# Step 4: Embed Chart into Google Slides
slide_id = slides_service.presentations().pages().create(
    presentationId=presentation_id,
    body={"slideLayoutReference": {"predefinedLayout": "BLANK"}}
).execute()["objectId"]

embedded_chart_request = {
    "requests": [
        {
            "createSheetsChart": {
                "objectId": "ChartObjectID",
                "spreadsheetId": spreadsheet_id,
                "chartId": 1,  # First chart added to spreadsheet
                "linkingMode": "LINKED",
                "elementProperties": {
                    "pageObjectId": slide_id,
                    "size": {
                        "height": {"magnitude": 4000000, "unit": "EMU"},
                        "width": {"magnitude": 6000000, "unit": "EMU"},
                    },
                    "transform": {
                        "scaleX": 1,
                        "scaleY": 1,
                        "translateX": 1000000,
                        "translateY": 1000000,
                        "unit": "EMU",
                    },
                },
            }
        }
    ]
}

slides_service.presentations().batchUpdate(
    presentationId=presentation_id, body=embedded_chart_request
).execute()
print(f"Chart added to Google Slides presentation {presentation_id}")


Spreadsheet ID: 1TNbkbcuGN4xUgi-TxVkPPyBKc0JM-_5A8Si_GDtgK60
Chart created in Google Sheets


SSLEOFError: EOF occurred in violation of protocol (_ssl.c:2427)